In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from ihm_analyse.lib import token_analysis as toka
from ihm_analyse.lib.helpers import (
    save_pickle, 
    load_pickle, 
    create_saving_folder,
)

from sentence_transformers import SentenceTransformer
import spacy
from pathlib import Path
import networkx as nx
import sys
import numpy as np

import os
from pathlib import Path

import networkx as nx
import numpy as np
import pandas as pd

from ihm_analyse import load_pickle
from ihm_analyse.lib.preprocess import merge_similarity_dupl
from ihm_analyse.lib.graphs import update_graph, get_graph_metadata


str_path = os.getcwd()
p = Path(str_path)
folder = list((p / 'results' / 'test_new2').glob('*'))
folder

C:\Users\foersterflorian\mambaforge\envs\ihm2\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


INFO:ihm_analyse.helpers:Loaded TOML config file successfully.


[WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-5_analyse_feature.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-1_build_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step_3_CosSim-FilterCandidates.xlsx'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-3_list_cosSim_dupl_candidates.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Token_Analysis_Step-1_build_token_graph.pickle'),
 WindowsPath('A:/Arbeitsaufgab

In [113]:
# constants and other pre-defined variables
DATA_SET_ID = 'Export4'

SAVE_PATH_FOLDER = f'./results/{DATA_SET_ID}/token_analysis/'
create_saving_folder(saving_path_folder=SAVE_PATH_FOLDER)

path = Path(SAVE_PATH_FOLDER)

INFO:ihm_analyse.helpers:Path >>./results/Export4/token_analysis/<< already exists and remained unchanged. If you want to overwrite this path, use parameter >>overwrite_existing<<.


In [95]:
nlp = spacy.load('de_dep_news_trf')

In [96]:
test_string = """
Das ist ein Test mit mehreren Sätzen. Ich bin so gut aufgelegt, dass ich jetzt einfach die Waschmaschine reparieren muss. 
Denn die Waschmaschine zu reparieren, ist eine Lebensaufgabe.
Und in diesem Leben schreibe ich mehrfache Anwendungen, weil ich noch in der Lagerhalle einkaufen muss. Das wird er sicher noch tun müssen.
Die Wartungsaufgabe wurde an Herrn Müller übertragen.
"""

In [97]:
doc = nlp(test_string)

In [98]:
G = nx.DiGraph()

In [99]:
toka.add_doc_info_to_graph(
    graph=G,
    doc=doc,
    weight=10,
)

In [100]:
G.adj

AdjacencyView({'Test': {'Satz': {'weight': 20}}, 'Satz': {}, 'auflegen': {'Waschmaschine': {'weight': 10}}, 'Waschmaschine': {'Lebensaufgabe': {'weight': 10}}, 'reparieren': {'Waschmaschine': {'weight': 20}}, 'Lebensaufgabe': {}, 'schreiben': {'Leben': {'weight': 10}, 'Anwendung': {'weight': 10}, 'Lagerhalle': {'weight': 10}}, 'Leben': {}, 'Anwendung': {}, 'Lagerhalle': {}, 'einkaufen': {'Lagerhalle': {'weight': 10}}, 'Wartungsaufgabe': {'Herr': {'weight': 10}, 'Müller': {'weight': 10}}, 'Herr': {'Müller': {'weight': 20}}, 'Müller': {}, 'übertragen': {'Herr': {'weight': 10}, 'Müller': {'weight': 10}}})

In [101]:
path_to_graph_export = SAVE_PATH_FOLDER + 'Directed_Graph_test3.graphml'
nx.write_graphml(G, path_to_graph_export)

In [102]:
df = nx.to_pandas_adjacency(G, dtype=np.uint64)
df

Test  Satz  auflegen  Waschmaschine  reparieren  \
Test                0    20         0              0           0   
Satz                0     0         0              0           0   
auflegen            0     0         0             10           0   
Waschmaschine       0     0         0              0           0   
reparieren          0     0         0             20           0   
Lebensaufgabe       0     0         0              0           0   
schreiben           0     0         0              0           0   
Leben               0     0         0              0           0   
Anwendung           0     0         0              0           0   
Lagerhalle          0     0         0              0           0   
einkaufen           0     0         0              0           0   
Wartungsaufgabe     0     0         0              0           0   
Herr                0     0         0              0           0   
Müller              0     0         0              0           0   
übertragen          0     0         0              0           0   

                 Lebensaufgabe  schreiben  Leben  Anwendung  Lagerhalle  \
Test                         0          0      0          0           0   
Satz                         0          0      0          0           0   
auflegen                     0          0      0          0           0   
Waschmaschine               10          0      0          0           0   
reparieren                   0          0      0          0           0   
Lebensaufgabe                0          0      0          0           0   
schreiben                    0          0     10         10          10   
Leben                        0          0      0          0           0   
Anwendung                    0          0      0          0           0   
Lagerhalle                   0          0      0          0           0   
einkaufen                    0          0      0          0          10   
Wartungsaufgabe              0          0      0          0           0   
Herr                         0          0      0          0           0   
Müller                       0          0      0          0           0   
übertragen                   0          0      0          0           0   

                 einkaufen  Wartungsaufgabe  Herr  Müller  übertragen  
Test                     0                0     0       0           0  
Satz                     0                0     0       0           0  
auflegen                 0                0     0       0           0  
Waschmaschine            0                0     0       0           0  
reparieren               0                0     0       0           0  
Lebensaufgabe            0                0     0       0           0  
schreiben                0                0     0       0           0  
Leben                    0                0     0       0           0  
Anwendung                0                0     0       0           0  
Lagerhalle               0                0     0       0           0  
einkaufen                0                0     0       0           0  
Wartungsaufgabe          0                0    10      10           0  
Herr                     0                0     0      20           0  
Müller                   0                0     0       0           0  
übertragen               0                0    10      10           0

In [103]:
G_undir = toka.convert_graph_to_undirected(graph=G)

INFO:ihm_analyse.token_analysis:Successfully converted graph to undirected edges. There are 13 edges in the graph.


In [89]:
df = nx.to_pandas_adjacency(G_undir, dtype=np.uint64)
df

Test  Satz  auflegen  Waschmaschine  reparieren  \
Test                0    20         0              0           0   
Satz               20     0         0              0           0   
auflegen            0     0         0             10           0   
Waschmaschine       0     0        10              0          20   
reparieren          0     0         0             20           0   
Lebensaufgabe       0     0         0             10           0   
schreiben           0     0         0              0           0   
Leben               0     0         0              0           0   
Anwendung           0     0         0              0           0   
Lagerhalle          0     0         0              0           0   
einkaufen           0     0         0              0           0   
Wartungsaufgabe     0     0         0              0           0   
Herr                0     0         0              0           0   
Müller              0     0         0              0           0   
übertragen          0     0         0              0           0   

                 Lebensaufgabe  schreiben  Leben  Anwendung  Lagerhalle  \
Test                         0          0      0          0           0   
Satz                         0          0      0          0           0   
auflegen                     0          0      0          0           0   
Waschmaschine               10          0      0          0           0   
reparieren                   0          0      0          0           0   
Lebensaufgabe                0          0      0          0           0   
schreiben                    0          0     10         10          10   
Leben                        0         10      0          0           0   
Anwendung                    0         10      0          0           0   
Lagerhalle                   0         10      0          0           0   
einkaufen                    0          0      0          0          10   
Wartungsaufgabe              0          0      0          0           0   
Herr                         0          0      0          0           0   
Müller                       0          0      0          0           0   
übertragen                   0          0      0          0           0   

                 einkaufen  Wartungsaufgabe  Herr  Müller  übertragen  
Test                     0                0     0       0           0  
Satz                     0                0     0       0           0  
auflegen                 0                0     0       0           0  
Waschmaschine            0                0     0       0           0  
reparieren               0                0     0       0           0  
Lebensaufgabe            0                0     0       0           0  
schreiben                0                0     0       0           0  
Leben                    0                0     0       0           0  
Anwendung                0                0     0       0           0  
Lagerhalle              10                0     0       0           0  
einkaufen                0                0     0       0           0  
Wartungsaufgabe          0                0    10      10           0  
Herr                     0               10     0      20          10  
Müller                   0               10    20       0          10  
übertragen               0                0    10      10           0

In [92]:
path_to_graph_export = SAVE_PATH_FOLDER + 'Undirected_Graph_test3.graphml'
nx.write_graphml(G_undir, path_to_graph_export)

---

In [114]:
list(path.parents[0].glob('*.pkl'))

[WindowsPath('results/Export4/Pipe-Preprocess1_Step-3_remove_NA.pkl'),
 WindowsPath('results/Export4/Pipe-Preprocess1_Step-5_analyse_feature.pkl'),
 WindowsPath('results/Export4/Pipe-Embedding1_Step-1_build_cosSim_matrix.pkl'),
 WindowsPath('results/Export4/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pkl'),
 WindowsPath('results/Export4/dupl_idx_pairs.pkl'),
 WindowsPath('results/Export4/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pkl')]

In [115]:
prep_data = load_pickle(path='./results/Export4/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pkl')
prep_data

INFO:ihm_analyse.helpers:Loaded file successfully.


entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      2163   
131               Tägliche Überprüfung der Ölabscheider   37      1619   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2681  vom Eisenkernvorrichtung (Teil vom Kettenlauf ...  136         1   
2680  Stand 15.07.2020 (Stöppel): Herr Langner (Toyo...  260         1   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                27  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2681                                              [515]                 1  
2680                                              [311]                 1  
2679                                              [415]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  

[5090 rows x 5 columns]

In [116]:
description_entries = prep_data[['entry', 'num_occur']]
description_entries

entry num_occur
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...     92592
33              Wöchentliche Sichtkontrolle / Reinigung      2163
131               Tägliche Überprüfung der Ölabscheider      1619
160               Wöchentliche Kontrolle der WC-Anlagen      1265
140        Halbjährliche Kontrolle des Stabbreithalters       687
...                                                 ...       ...
2681  vom Eisenkernvorrichtung (Teil vom Kettenlauf ...         1
2680  Stand 15.07.2020 (Stöppel): Herr Langner (Toyo...         1
2679  Zahnräder der Laufkatze verschlissen Ersatztei...         1
2677  Schalter für Bühne Schwenken abgerissen, bitte...         1
2676                                  Docke angefahren!         1

[5090 rows x 2 columns]

In [117]:
data_token_analysis = description_entries.iloc[:1000,:].copy()
data_token_analysis = description_entries.copy()

In [118]:
graph = toka.build_token_graph(data=data_token_analysis, model=nlp)

100%|██████████████████████████████████████████████████████████████████████████████| 5090/5090 [03:58<00:00, 21.30it/s]

INFO:ihm_analyse.token_analysis:Graph properties: 6383 Nodes, 19489 Edges
INFO:ihm_analyse.token_analysis:Node memory: 393.35 KB
INFO:ihm_analyse.token_analysis:Edge memory: 1065.80 KB
INFO:ihm_analyse.token_analysis:Total memory: 1459.16 KB


In [123]:
path_to_graph_dir_export = SAVE_PATH_FOLDER + 'Directed_Graph_full.graphml'
nx.write_graphml(graph, path_to_graph_dir_export)
path_to_graph_undir_export = SAVE_PATH_FOLDER + 'Undirected_Graph_full.graphml'
graph_undir = toka.convert_graph_to_undirected(graph=graph)
nx.write_graphml(graph_undir, path_to_graph_undir_export)

INFO:ihm_analyse.token_analysis:Successfully converted graph to one with undirected edges.
INFO:ihm_analyse.token_analysis:Undirected Graph properties: 6383 Nodes, 18977 Edges


In [110]:
len(graph.nodes)

6383

In [111]:
len(graph.edges)

19489

INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: sentence-transformers/all-mpnet-base-v2
INFO:sentence_transformers.SentenceTransformer:Use pytorch device_name: cpu


In [16]:
import os
from pathlib import Path

from ihm_analyse import SAVE_PATH_FOLDER, THRESHOLD_EDGE_WEIGHT, TokenGraph, load_pickle
from ihm_analyse.predefined_pipes import pipe_token_analysis
from ihm_analyse.lib.helpers import load_toml_config

str_path = os.getcwd()
p = Path(str_path)
folder = list((p / 'results' / 'test_new2').glob('*'))
folder

[WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-5_analyse_feature.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-1_build_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step_3_CosSim-FilterCandidates.xlsx'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-3_list_cosSim_dupl_candidates.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Token_Analysis_Step-1_build_token_graph.pickle'),
 WindowsPath('A:/Arbeitsaufgab

In [2]:
def run_token_analysis(
    preprocessed_data,
):
    (token_graph,) = pipe_token_analysis.run(starting_values=(preprocessed_data,))
    token_graph.save_graph(SAVE_PATH_FOLDER, directed=False)
    token_graph.to_pickle(SAVE_PATH_FOLDER, 
                     filename=f'{pipe_token_analysis.name}-TokenGraph')
    token_graph.save_graph(SAVE_PATH_FOLDER, directed=False)
    token_graph.to_pickle(SAVE_PATH_FOLDER, 
                     filename=f'{pipe_token_analysis.name}-TokenGraph')
    # filter graph by edge weight and remove single nodes (no connection)
    tk_graph_filtered = token_graph.filter_by_edge_weight(THRESHOLD_EDGE_WEIGHT)
    tk_graph_filtered = tk_graph_filtered.filter_by_node_degree(1)
    tk_graph_filtered.save_graph(SAVE_PATH_FOLDER,
                                 filename='TokenGraph-filtered',
                                 directed=False)
    tk_graph_filtered.to_pickle(SAVE_PATH_FOLDER,
                     filename=f'{pipe_token_analysis.name}-TokenGraph-filtered')
    
    return token_graph, tk_graph_filtered

In [19]:
str_path = os.getcwd()
p = Path(str_path)
config_p = p / 'ihm_analyse' / 'config.toml'

In [20]:
config_p

WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/ihm_analyse/config.toml')

In [22]:
conf = load_toml_config(config_p)
conf

INFO:ihm_analyse.helpers:Loaded TOML config file successfully.


{'common': {'paths': {'results': './results/test_new2/',
   'dataset': './01_2_Rohdaten_neu/Export4.csv'}},
 'export_filenames': {'filename_cossim_filter_candidates': 'CosSim-FilterCandidates'},
 'preprocess': {'date_cols': ['VorgangsDatum',
   'ErledigungsDatum',
   'Arbeitsbeginn',
   'ErstellungsDatum'],
  'threshold_amount_characters': 5,
  'threshold_similarity': 0.8},
 'token_analysis': {'threshold_edge_weight': 150}}

In [24]:
p

WindowsPath('A:/Arbeitsaufgaben/Instandhaltung')

In [28]:
filename = r'*Pipe-Merge_Duplicates_Step-1*'
folder = list(SAVE_PATH_FOLDER.glob(filename))[0]
folder

WindowsPath('results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pickle')

In [6]:
# dataset
res = load_pickle(folder[-6])
data = res[0]

INFO:ihm_analyse.helpers:Loaded file successfully.


In [7]:
data

entry  len num_occur  \
162   Tägliche Wartungstätigkeiten nach Vorgabe des ...   66     92592   
33              Wöchentliche Sichtkontrolle / Reinigung   39      3111   
131               Tägliche Überprüfung der Ölabscheider   37      1619   
160               Wöchentliche Kontrolle der WC-Anlagen   37      1265   
140        Halbjährliche Kontrolle des Stabbreithalters   44       687   
...                                                 ...  ...       ...   
2680  Stand 15.07.2020 (Stöppel): Herr Langner (Toyo...  260         1   
2679  Zahnräder der Laufkatze verschlissen Ersatztei...  170         1   
2677  Schalter für Bühne Schwenken abgerissen, bitte...  126         1   
2676                                  Docke angefahren!   17         1   
6799  Befestigung Deckel für Batteriefach defekt    ...  107         2   

                                          assoc_obj_ids num_assoc_obj_ids  
162   [0, 17, 41, 42, 43, 44, 45, 46, 47, 51, 52, 53...               206  
33    [301, 304, 305, 313, 314, 323, 329, 331, 332, ...                74  
131                                [0, 970, 2134, 2137]                 4  
160   [1352, 1353, 1354, 1684, 1685, 1686, 1687, 168...                11  
140   [51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 6...               166  
...                                                 ...               ...  
2680                                              [311]                 1  
2679                                              [415]                 1  
2677                                              [323]                 1  
2676                                              [176]                 1  
6799                                         [306, 326]                 2  

[4582 rows x 5 columns]

In [8]:
preprocessed_data_trunc = data[['entry', 'num_occur']].iloc[:20,:].copy()
preprocessed_data_trunc = data[['entry', 'num_occur']].copy()

In [9]:
tk_graph, tk_graph_filtered = run_token_analysis(preprocessed_data_trunc)

INFO:ihm_analyse.pipelines:Starting processing pipeline >>Token_Analysis<<...


100%|██████████████████████████████████████████████████████████████████████████████| 4582/4582 [03:36<00:00, 21.16it/s]

INFO:ihm_analyse.graphs:Graph properties: 6200 Nodes, 18770 Edges
INFO:ihm_analyse.graphs:Node memory: 381.88 KB
INFO:ihm_analyse.graphs:Edge memory: 1026.48 KB
INFO:ihm_analyse.graphs:Total memory: 1408.36 KB


INFO:ihm_analyse.graphs:Successfully converted graph to one with undirected edges.
INFO:ihm_analyse.graphs:Graph properties: 6200 Nodes, 18297 Edges
INFO:ihm_analyse.graphs:Node memory: 381.88 KB
INFO:ihm_analyse.graphs:Edge memory: 1000.62 KB
INFO:ihm_analyse.graphs:Total memory: 1382.50 KB
INFO:ihm_analyse.graphs:Graph properties: 6200 Nodes, 18297 Edges
INFO:ihm_analyse.graphs:Node memory: 381.88 KB
INFO:ihm_analyse.graphs:Edge memory: 1000.62 KB
INFO:ihm_analyse.graphs:Total memory: 1382.50 KB
INFO:ihm_analyse.helpers:Saved file successfully under results\test_new2\Pipe-Token_Analysis_Step-1_build_token_graph.pickle
INFO:ihm_analyse.pipelines:Processing pipeline >>Token_Analysis<< successfully ended.
INFO:ihm_analyse.graphs:Successfully saved graph as GraphML file under results\test_new2\TokenGraph.graphml.
INFO:ihm_analyse.helpers:Saved file successfully under results\test_new2\Token_Analysis-TokenGraph.pickle
INFO:ihm_analyse.graphs:Successfully saved graph as GraphML file under 

In [10]:
tk_graph

TokenGraph(name: TokenGraph, number of nodes: 6200, number of edges: 18770)

In [29]:
tk_graph.metadata_directed

{'num_nodes': 6200,
 'num_edges': 18770,
 'min_edge_weight': 1,
 'max_edge_weight': 92690,
 'node_memory': 391043,
 'edge_memory': 1051120,
 'total_memory': 1442163}

In [30]:
tk_graph.metadata_undirected

{'num_nodes': 6200,
 'num_edges': 18297,
 'min_edge_weight': 1,
 'max_edge_weight': 92690,
 'node_memory': 391043,
 'edge_memory': 1024632,
 'total_memory': 1415675}

In [15]:
tk_graph_filtered

TokenGraph(name: TokenGraph, number of nodes: 147, number of edges: 179)

In [13]:
tk_graph_filtered.metadata_undirected

{'num_nodes': 147,
 'num_edges': 177,
 'min_edge_weight': 153,
 'max_edge_weight': 92690,
 'node_memory': 9487,
 'edge_memory': 9912,
 'total_memory': 19399}

In [11]:
folder = list((p / 'results' / 'test_new2').glob('*'))
folder

[WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-3_remove_NA.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-TargetFeature_Step-5_analyse_feature.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-1_build_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-2_filt_thresh_cosSim_matrix.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step_3_CosSim-FilterCandidates.xlsx'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Embedding1_Step-3_list_cosSim_dupl_candidates.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Merge_Duplicates_Step-1_merge_similarity_dupl.pickle'),
 WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Token_Analysis_Step-1_build_token_graph.pickle'),
 WindowsPath('A:/Arbeitsaufgab

In [3]:
p = folder[-2]
p

WindowsPath('A:/Arbeitsaufgaben/Instandhaltung/results/test_new2/Pipe-Token_Analysis_Step-1_build_token_graph.pickle')

In [4]:
ret = load_pickle(p)
ret

INFO:ihm_analyse.helpers:Loaded file successfully.


(<ihm_analyse.lib.graphs.TokenGraph at 0x2451a5a07d0>,)

In [5]:
tk_graph = ret[0]

In [9]:
deg_view = tk_graph.degree

In [14]:
for i, view in enumerate(tk_graph.nodes):
    print(tk_graph.degree[view])
    if i == 5:
        break

8
20
2
23
47
123


In [12]:
tk_graph.degree['Wartungstätigkeit']

8